In [27]:
import osmnx as ox
import folium
from IPython.display import display
import requests
import json

# Define the Overpass API query for Transjakarta network
query = """
[out:json][timeout:25];
(
  nwr["route"="bus"]["type"="route"]({{bbox}});
  nwr["route"="train"]["type"="route"]["network"="KAI Commuter"]({{bbox}});
);
out geom;
"""

# Function to get bounding box for Pancoran
def get_place_bbox(place_name):
    gdf = ox.geocode_to_gdf(place_name)
    bounds = gdf.total_bounds
    return f"{bounds[1]},{bounds[0]},{bounds[3]},{bounds[2]}"

# Get bounding box for Pancoran
bbox = get_place_bbox("Jakarta")

# Replace {{bbox}} in the query
query = query.replace("{{bbox}}", bbox)

# Fetch data from Overpass API
overpass_url = "http://overpass-api.de/api/interpreter"
import os
import json

cache_file = 'overpass_cache.json'

if False and os.path.exists(cache_file):
    with open(cache_file, 'r') as f:
        data = json.load(f)
else:
    response = requests.get(overpass_url, params={'data': query})
    data = response.json()
    # Dump the full overpass_cache
    with open('overpass_cache.json', 'w') as f:
        json.dump(data, f, indent=2)

    # Create a lite version with only the first 30 results
    lite_data = {
        "version": data["version"],
        "generator": data["generator"],
        "osm3s": data["osm3s"],
        "elements": data["elements"][:30]
    }

    # Dump the lite version
    with open('overpass_lite.json', 'w') as f:
        json.dump(lite_data, f, indent=2)

    print("Full data saved to 'overpass_cache.json'")
    print("Lite version (first 30 results) saved to 'overpass_lite.json'")


Full data saved to 'overpass_cache.json'
Lite version (first 100 results) saved to 'overpass_lite.json'


In [25]:
from haversine import haversine
from collections import defaultdict

# Create a map centered on Jakarta
jakarta_coords = (-6.2088, 106.8456)  # Latitude and longitude for Jakarta
m = folium.Map(location=jakarta_coords, zoom_start=11, tiles='CartoDB positron')

# Create a FeatureGroup for each relation
feature_groups = defaultdict(folium.FeatureGroup)

# Iterate through the relations (routes) in the data
for element in data['elements']:
    if element['type'] == 'relation':
        relation_id = element['id']
        route_name = element.get('tags', {}).get('name', f'Unnamed route {relation_id}')
        # Generate a unique color for this relation
        color = f'#{abs(hash(route_name)) % 0xFFFFFF:06x}'
        
        # Create a new FeatureGroup for this relation if it doesn't exist
        if relation_id not in feature_groups:
            feature_groups[relation_id] = folium.FeatureGroup(name=route_name, show=True)
        
        # Collect all coordinates for this route
        coordinates = []
        for member in element['members']:
            if member['type'] == 'way' and 'geometry' in member:
                for point in member['geometry']:
                    if not coordinates or haversine(coordinates[-1], (point['lat'], point['lon'])) < 2:
                        coordinates.append((point['lat'], point['lon']))
        
        # Apply a small offset to the coordinates
        offset = 0.00001 * (relation_id % 10 - 5)  # This creates a range of offsets from -0.0005 to 0.0005
        offset_coordinates = [(lat + offset, lon + offset) for lat, lon in coordinates]
        
        # Draw the route on the map
        folium.PolyLine(
            locations=offset_coordinates,
            color=color,
            weight=2,
            opacity=0.8,
            tooltip=route_name
        ).add_to(feature_groups[relation_id])

# Add all feature groups to the map in alphabetical order
for fg in sorted(feature_groups.values(), key=lambda x: x.layer_name):
    fg.add_to(m)

# Add layer control to toggle routes on/off
folium.LayerControl().add_to(m)

# Display the map
display(m)
